# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [10 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
from google.colab import drive
drive.mount('/content/drive')

%cd /content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis/
%ls

Mounted at /content/drive
/content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis
Agent_trainer_notebooks/          __pycache__/          VPP_environment.py
data/                             README.md             VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  Simulator_notebooks/  wandb/
log.log                           trained_models/


In [3]:
# #Cloning repository and changing directory
# !git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
# %cd RL_VPP_Thesis/
# %ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7facc6ea01d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 15
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 15, 'EVs_n_max': 783, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14085.73 , over-consume=kWh  32236.88 , under-consume=kWh  18151.15 , Total_cost=€  663.87 , overcost=€  1172.42 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14124.23 , over-consume=kWh  33139.41 , under-consume=kWh  19015.18 , Total_cost=€  663.91 , overcost=€  1206.3 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6324.36 , over-consume=KWh  3091.38 , under-consume=KWh  9415.74 , Total_cost=€  -131.56 , Overcost=€  113.43 
 EV_INFO: Av.EV_energy_leaving=kWh  68.6 , Std.EV_energy_leaving=kWh  24.03 , EV_departures =  782 , EV_queue_left =  0
SCORE:  Cumulative_reward= 312688.94 - Step_rewars (load_t= 291091.85, EVs_energy_t= 15726.26)
 - Final_rewards (EVs_energy= 12262.12, Overconsume= -2991.18, Underconsume= -5534.43, Overcost= 2134.33)
Episode:1 Score:312688.9449899887


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000  55.038242  53.096100   0.000000   
2022-01-01 00:15:00  48.826286  54.133205  53.346100  35.307587   
2022-01-01 00:30:00  49.076286  53.583118  52.796013  35.557587   
2022-01-01 00:45:00  49.326286  53.121716  52.334610  35.807587   
2022-01-01 01:00:00  49.576286  52.766399  51.979294  36.057587   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  83.170425   0.000000  99.989998  37.001656   
2022-06-06 05:00:00  83.170425   0.000000  99.989998  36.751656   
2022-06-06 05:15:00  83.170425   0.000000  99.989998  36.501656   
2022-06-06 05:30:00  83.170425   0.000000  99.989998  36.501656   
2022-06-06 05:45:00  83.170425   0.000000  99.989998  36.501656   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 2, 1, 2]   
2022-01-01 00:15:00  [2351, 2349, 2348, 2350]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [2351, 2349, 2348, 2350]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [2351, 2349, 2348, 2350]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [2351, 2349, 2348, 2350]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00     [2673, 0, 2674, 2675]  [0, 0, 1, 2]   
2022-06-06 05:00:00     [2673, 0, 2674, 2675]  [0, 0, 1, 2]   
2022-06-06 05:15:00     [2673, 0, 2674, 2675]  [0, 0, 1, 0]   
2022-06-06 05:30:00     [2673, 0, 2674, 2675]  [0, 0, 1, 0]   
2022-06-06 05:45:00     [2673, 0, 2674, 2675]  [0, 0, 1, 0]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  2.673117e+00    15.000000   
2022-01-01 00:15:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 00:30:00    [False, True, True, False] -4.440892e-16    15.000000   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [False, True, True, False]  1.110223e-16    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00    [True, True, False, False] -9.721995e+00   -12.955564   
2022-06-06 05:00:00    [True, True, False, False] -1.275112e+01   -15.158185   
2022-06-06 05:15:00    [True, True, False, False] -1.515819e+01   -12.222906   
2022-06-06 05:30:00    [True, True, False, False] -1.194520e+01   -12.379142   
2022-06-06 05:45:00    [True, True, False, False] -1.211706e+01   -12.859520   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0 -12.955564  
2022-06-06 05:00:00        0.0 -15.158185  
2022-06-06 05:15:00        0.0 -12.222906  
2022-06-06 05:30:00        0.0 -12.379142  
2022-06-06 05:45:00        0.0 -12.859520  

[15000 rows x 11 columns]

In [25]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_Elvis_comparison()

In [28]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [29]:
env.plot_rewards_stats()

In [30]:
env.plot_EVs_kpi()

In [31]:
env.plot_load_kpi()

In [32]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [33]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3133, Arrival time: 2022-01-01 13:30:00, Parking_time: 24, Leaving_time: 2022-01-02 13:30:00, SOC: 0.6096201688879868, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 3915, Arrival time: 2022-12-31 23:45:00, Parking_time: 22.12793241098197, Leaving_time: 2023-01-01 21:52:40.556680, SOC: 0.35810571509344985, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5382.52 , over-consume=kWh  28540.75 , under-consume=kWh  23158.23 , Total_cost=€  290.6 , overcost=€  1236.31 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15


In [34]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [35]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [36]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5745.17 , over-consume=kWh  29671.68 , under-consume=kWh  23926.51 , Total_cost=€  361.4 , overcost=€  1329.81 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10206.15 , over-consume=KWh  1592.28 , under-consume=KWh  11798.44 , Total_cost=€  -385.83 , Overcost=€  70.03 
 EV_INFO: Av.EV_energy_leaving=kWh  74.73 , Std.EV_energy_leaving=kWh  22.44 , EV_departures =  780 , EV_queue_left =  0
SCORE:  Cumulative_reward= 338728.48 - Step_rewars (load_t= 291399.55, EVs_energy_t= 30171.03)
 - Final_rewards (EVs_energy= 14033.7, Overconsume= -1374.02, Underconsume= -5495.84, Overcost= 9994.05)
Episode:1 Score:338728.4790509479


In [37]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [38]:
VPP_table.head(15000)

0    1    2    3        EVs_id       actions  \
time                                                                  
2022-01-01 00:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                  ...  ...  ...  ...           ...           ...   
2022-06-06 04:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-06-06 05:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-06-06 05:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-06-06 05:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-06-06 05:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 2, 2]   

                                       mask_truth       load  load_reward  \
time                                                                        
2022-01-01 00:00:00   [False, False, False, True]  -4.058354    -5.081536   
2022-01-01 00:15:00   [False, False, False, True]  -4.089689    -4.303589   
2022-01-01 00:30:00   [False, False, False, True]  -3.582153    -4.065516   
2022-01-01 00:45:00   [False, False, False, True]  -3.439309    -5.202420   
2022-01-01 01:00:00    [False, True, False, True]  -4.222662    -5.202624   
...                                           ...        ...          ...   
2022-06-06 04:45:00  [False, False, False, False] -11.014682   -14.039054   
2022-06-06 05:00:00  [False, False, False, False] -13.942960   -14.813320   
2022-06-06 05:15:00  [False, False, False, False] -14.794652   -13.855108   
2022-06-06 05:30:00  [False, False, False, False] -13.740619   -14.030191   
2022-06-06 05:45:00  [False, False, False, False] -13.933210   -15.486146   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.081536  
2022-01-01 00:15:00        0.0  -4.303589  
2022-01-01 00:30:00        0.0  -4.065516  
2022-01-01 00:45:00        0.0  -5.202420  
2022-01-01 01:00:00        0.0  -5.202624  
...                        ...        ...  
2022-06-06 04:45:00        0.0 -14.039054  
2022-06-06 05:00:00        0.0 -14.813320  
2022-06-06 05:15:00        0.0 -13.855108  
2022-06-06 05:30:00        0.0 -14.030191  
2022-06-06 05:45:00        0.0 -15.486146  

[15000 rows x 11 columns]

In [39]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [40]:
env.plot_VPP_Elvis_comparison()

In [41]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_rewards_stats()

In [43]:
env.plot_EVs_kpi()

In [44]:
env.plot_load_kpi()

In [45]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [46]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5482, Arrival time: 2022-01-01 12:00:00, Parking_time: 24, Leaving_time: 2022-01-02 12:00:00, SOC: 0.39281050080373414, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6264, Arrival time: 2022-12-31 15:30:00, Parking_time: 23.646151316832807, Leaving_time: 2023-01-01 15:08:46.144741, SOC: 0.47676078120492305, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  558.1 , over-consume=kWh  26188.97 , under-consume=kWh  25630.88 , Total_cost=€  191.0 , overcost=€  1130.02 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56


In [47]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [48]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [49]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  392.5 , over-consume=kWh  26247.97 , under-consume=kWh  25855.48 , Total_cost=€  155.33 , overcost=€  1102.28 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -12870.41 , over-consume=KWh  1553.44 , under-consume=KWh  14423.85 , Total_cost=€  -459.05 , Overcost=€  64.94 
 EV_INFO: Av.EV_energy_leaving=kWh  77.61 , Std.EV_energy_leaving=kWh  21.8 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 309896.19 - Step_rewars (load_t= 259326.26, EVs_energy_t= 35828.64)
 - Final_rewards (EVs_energy= 14243.86, Overconsume= -1599.32, Underconsume= -6709.96, Overcost= 8806.7)
Episode:1 Score:309896.1945210133


In [50]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [51]:
VPP_table.head(14995)

0    1          2          3              EVs_id  \
time                                                                      
2022-01-01 00:00:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:30:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:45:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 01:00:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
...                  ...  ...        ...        ...                 ...   
2022-06-06 03:30:00  0.0  0.0  83.869957  79.513046  [0, 0, 7381, 7382]   
2022-06-06 03:45:00  0.0  0.0  84.412857  80.055946  [0, 0, 7381, 7382]   
2022-06-06 04:00:00  0.0  0.0  85.251137  80.894226  [0, 0, 7381, 7382]   
2022-06-06 04:15:00  0.0  0.0  86.189140  81.832230  [0, 0, 7381, 7382]   
2022-06-06 04:30:00  0.0  0.0  86.956589  82.599678  [0, 0, 7381, 7382]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True] -3.175294   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True] -3.741196   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True] -2.970961   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True] -3.454874   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True] -4.973915   
...                           ...                          ...       ...   
2022-06-06 03:30:00  [0, 2, 1, 1]    [True, False, True, True]  0.000000   
2022-06-06 03:45:00  [0, 2, 1, 1]    [True, False, True, True]  0.000000   
2022-06-06 04:00:00  [0, 2, 1, 1]    [True, False, True, True]  0.000000   
2022-06-06 04:15:00  [0, 2, 1, 1]    [True, False, True, True]  0.000000   
2022-06-06 04:30:00  [0, 2, 1, 1]    [True, False, True, True]  0.000000   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    -4.568660        0.0  -4.568660  
2022-01-01 00:15:00    -3.284935        0.0  -3.284935  
2022-01-01 00:30:00    -4.091456        0.0  -4.091456  
2022-01-01 00:45:00    -5.885378        0.0  -5.885378  
2022-01-01 01:00:00    -6.722393        0.0  -6.722393  
...                          ...        ...        ...  
2022-06-06 03:30:00    15.000000        0.0  15.000000  
2022-06-06 03:45:00    15.000000        0.0  15.000000  
2022-06-06 04:00:00    15.000000        0.0  15.000000  
2022-06-06 04:15:00    15.000000        0.0  15.000000  
2022-06-06 04:30:00    15.000000        0.0  15.000000  

[14995 rows x 11 columns]

In [52]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
env.plot_VPP_Elvis_comparison()

In [54]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_rewards_stats()

In [56]:
env.plot_EVs_kpi()

In [57]:
env.plot_actions_kpi()

In [58]:
env.plot_load_kpi()

In [59]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [60]:
#env.close()